# Automated virtual spectrometer example offline analysis

This is an example notebook showing how to use the `pes_to_spec` infrastructure in this package. The objective here is to calibrate the photo-electron spectrometer data automatically. This is done by using data from one "training" run that contains data from both the photo-electron spectrometer (PES), XGM and the grating spectrometer and then using the correlation between them to calibrate the PES data when no grating spectrometer is available.

This notebook includes the main analysis to simple get a calibrated PES spectrum using this automated method, as well as further analyses on the output in a second section. The objective of the second sections are only to validate results and may probably be skipped in most cases, if one needs only the PES spectrum.

We start by importing some modules. The key module here is called `pes_to_spec`. It can be cloned from its repository using the following command (for example) in Maxwell:

`git clone https://git.xfel.eu/machineLearning/pes_to_spec.git`

After that the notebook in the directory `pes_to_spec/notebook` can be opened and executed using the kernel `xfel (current)`. The specialized environment mentioned in the `README.md` file of the package may offer a slightly better performance and allow for expert features, but this is not necessary for the standard analysis.

## Core automated virtual spectromater usage

Here we expand on the usage of the virtual spectrometer. We assume that 2 runs of data have been collected. A first run contains both XGM, PES and grating spectrometer data.

A test run may contain only the XGM and PES data. If the test run contains also the grating spectrometer, it can be used also for validation, but in a real use-case this may not be available.

In [1]:
import sys
# add the pes_to_spec main directory
# (change this depending on where you started the notebook if needed, or comment it out if you have done pip install in pes_to_spec)
sys.path.append('..')

# you meay need to do pip install matplotlib seaborn extra_data for this notebook, additionally
# for this notebook the following packages are needed:
# pip install "numpy>=1.21" "scipy>=1.6" "scikit-learn>=1.2.0" torch torchbnn  matplotlib seaborn extra_data

In [2]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.gridspec import GridSpec 
import seaborn as sns

import lmfit
import scipy
from extra_data import open_run, by_id
from itertools import product
from pes_to_spec.model import get_model_with_resolution, Model, matching_ids, matching_two_ids

from typing import Any, Dict

### Input data

Note that the data in the training run must be large enough, compared to the number of model parameters.

Only the grating spectrometer, PES and XGM data is used for training, while only the PES and XGM data is needed for testing.
However, more data is collected here to validate the results.

Please adjust the proposal number, run number and name of the devices below as needed. Specifically, note that the grating spectrometer name changes depending on where the data has been collected. If unsure, try `run.info()` to check if the it contains `SPECTROMETER_SCS_NAVITAR`, `SPECTROMETER_SQS_NAVITAR` or `SPECTROMETER_SXP_NAVITAR`, etc.

Additionally, please check that the list of PES channels includes the channels active during the runs. It may be that data from all channels are written to disk, but not all channels are active (in which case they contain only noise). This would not hurt the procedure, but could lead to erroneous comparison between the results.

In [3]:
run = open_run(proposal=900331, run=69)
run_test = open_run(proposal=900331, run=70)

# useful names to avoid repeating it all over the notebook, in case they ever change
grating_name = "SA3_XTD10_SPECT/MDL/SPECTROMETER_SCS_NAVITAR:output"
pes_name = "SA3_XTD10_PES/ADC/1:network"
xgm_name = "SA3_XTD10_XGM/XGM/DOOCS:output"

pres_name = "SA3_XTD10_PES/GAUGE/G30310F"
volt_name = "SA3_XTD10_PES/MDL/DAQ_MPOD"

# PES channels
channels = [f"channel_{i}_{l}" for i, l in product([1, 3, 4], ["A", "B", "C", "D"])]

def get_gas(run) -> str:
    """Get gas in chamber for logging."""
    gas_sources = [
                  "SA3_XTD10_PES/DCTRL/V30300S_NITROGEN",
                  "SA3_XTD10_PES/DCTRL/V30310S_NEON",
                  "SA3_XTD10_PES/DCTRL/V30320S_KRYPTON",
                  "SA3_XTD10_PES/DCTRL/V30330S_XENON",
              ]
    gas_active = list()
    for gas in gas_sources:
        # check if this gas source is interlocked
        if gas in run.all_sources and run[gas, "interlock.AActionState.value"].ndarray().sum() == 0:
            # it is not, so this gas was used
            gas_active += [gas.split("/")[-1].split("_")[-1]]
    gas = "_".join(gas_active)
    return gas

def get_tids(run) -> np.ndarray:
    """Get which train IDs contain all necessary inputs for training."""
    if grating_name in run.all_sources:
        spec_tid = run[grating_name, "data.trainId"].ndarray()
    else:
        spec_tid = None
    pes_tid = run[pes_name, "digitizers.trainId"].ndarray()
    xgm_tid = run[xgm_name, "data.trainId"].ndarray()

    # match tids to be sure we have all inputs:
    if spec_tid is None:
        tids = matching_two_ids(pes_tid, xgm_tid)
    else:
        tids = matching_ids(spec_tid, pes_tid, xgm_tid)

    return tids

def get_data(run, tids) -> Dict[str, Any]:
    """Get all relevant data."""
    data = dict()
    data["intensity"] = run[xgm_name, "data.intensitySa3TD"].select_trains(by_id[tids]).ndarray()[:, 0][:, np.newaxis]
    data["pes"] = {ch: run[pes_name,
                           f"digitizers.{ch}.raw.samples"].select_trains(by_id[tids]).ndarray()
                    for ch in channels}
    # this may not be available in testing
    if grating_name in run.all_sources:
        data["grating"] = run[grating_name, "data.intensityDistribution"].select_trains(by_id[tids]).ndarray()
        data["energy"] = run[grating_name, "data.photonEnergy"].select_trains(by_id[tids]).ndarray()
    # only for validation
    data["pressure"] = run[pres_name, "value"].select_trains(by_id[tids]).ndarray()
    data["voltage"] = run[volt_name, "u213.value"].select_trains(by_id[tids]).ndarray()
    data["gas"] = get_gas(run)
    return data


In [4]:

# get the matched train IDs
tids = get_tids(run)
test_tids = get_tids(run_test)

# get the data
data = get_data(run, tids)
data_test = get_data(run_test, test_tids)


Now the `data` and `data_test` dictionaries contain the necessary information about the training and test runs.
The code above also selected only entries with train IDs on which at least SPEC, PES and XGM were present.

Note that for training, it is assumed that only one pulse is present. For testing there is no such requirement.

First output some general information about the conditions of the measurement device.

The method expects the run conditions to be the same in training and inference, so check that there is not a significant deviation here.

In [5]:
print(f"Gas in training: {data['gas']}")
print(f"Gas in testing: {data_test['gas']}")

Gas in training: NEON
Gas in testing: NEON


In [6]:
print(f"Voltage in training: {np.mean(data['voltage']):0.2f} +/- {np.std(data['voltage']):0.2f}")
print(f"Voltage in testing: {np.mean(data_test['voltage']):0.2f} +/- {np.std(data_test['voltage']):0.2f}")

Voltage in training: -116.01 +/- 0.01
Voltage in testing: -116.00 +/- 0.01


In [7]:
print(f"Pressure in training: {np.mean(data['pressure']):0.2e} +/- {np.std(data['pressure']):0.2e}")
print(f"Pressure in testing: {np.mean(data_test['pressure']):0.2e} +/- {np.std(data_test['pressure']):0.2e}")

Pressure in training: 1.29e-06 +/- 3.95e-08
Pressure in testing: 1.29e-06 +/- 3.91e-08


### Using the virtual spectrometer

Now we will actually train the model. We do that by creating a `Model` object (from `pes_to_spec`) and fitting the data. It requires the PES intensity, the grating spec. intensity, the energy axis from grating spec., as well as the energy measured in the XGM (which has better resolution than the integral of the PES).

We actually do this twice: in the first time we do it without any preprocessing on the grating spectrometer data. After that step, we record the maximum resolution achievable with the virtual spectrometer and then redo the estimate using the discovered resolution to pre-process the grating spectrometer data, so that this information is taken into account in the uncertainty estimate.

The work of calculating the expected resolution and adapting to it is done by the `get_model_with_resolution`

In [15]:
model, resolution = get_model_with_resolution(data['pes'],
                                              data['grating'],
                                              data['energy'],
                                              data['intensity'],
                                              channels=channels,
                                              )
print(f"Resolution: {resolution:.2f} eV")

Checking data quality in high-resolution data.
Selected 7165 of 7165 samples
Fitting PCA on low-resolution data.
Using 556 comp. for PES PCA.
Fitting PCA on high-resolution data.
Using 24 comp. for grating spec. PCA.
Fitting outlier detection
Fitting model.
Calculate PCA unc. on high-resolution data.
Calculate transfer function
Resolution: 0.8169395778859361
Calculate PCA on channel_1_A
Calculate PCA on channel_1_B
Calculate PCA on channel_1_C
Calculate PCA on channel_1_D
Calculate PCA on channel_3_A
Calculate PCA on channel_3_B
Calculate PCA on channel_3_C
Calculate PCA on channel_3_D
Calculate PCA on channel_4_A
Calculate PCA on channel_4_B
Calculate PCA on channel_4_C
Calculate PCA on channel_4_D
End of fit.
Resolution: 0.82 eV


We can save the resulting model for later usage using the `save` method and then reload it later with the `load` function as shown below. This can be useful if one wants to reuse information at a later stage.

In [16]:
# save it for later usage:
model.save("model.joblib")

In [17]:
# load a model -- you can skip the fit above if you just start from this line
#model = Model.load("model.joblib")

Now we can use this mapping on new data. In this example, we try it in the test dataset mentioned.

In [18]:
pred = model.predict(data_test['pes'], pulse_energy=data_test['intensity'])

# add the references in this array in the same array format, so we can plot them later
pred["energy"] = model.get_energy_values()
pred['grating'] = data_test['grating'][:, np.newaxis, :]
# let us show also how the virtual spectrometer looks like smeared by the virtual spectrometer resolution
pred['grating_smooth'] = model.preprocess_high_res(data_test['grating'], resolution=model.resolution)[:, np.newaxis, :]

Let's try to predict in the independent run in the test dataset. The performance of the model varies a lot if the beam intensity is very different from the training one. To ensure we take a train ID to visualize that is relatively high intensity, we sort the train IDs by XGM intensity and then choose the highest intensity one.
One could try other train IDs.

For train IDs with close to zero beam intensity, there is a relatively larger error, since the training data did not contain any of those samples and the signal-to-noise ratio is relatively high.

In [19]:
# choose train ID of the test dataset by XGM intensity
test_intensity = np.argsort(data_test['intensity'][:,0])
example_tid = test_intensity[-1]

Now we can actually plot it.

In [20]:
def plot(data):
    """Plot prediction and expectation."""
    fig = plt.figure(figsize=(12, 8))
    gs = GridSpec(1, 1)
    ax = fig.add_subplot(gs[0, 0])
    ax.plot(data["energy"], data["grating"], c='b', lw=3, label="Grating spec. measurement")
    ax.plot(data["energy"], data["grating_smooth"], c='g', lw=3, label="Smoothened grating spec. measurement")
    ax.plot(data["energy"], data["expected"], c='r', ls='--', lw=3, label="Prediction")
    ax.fill_between(data["energy"], data["expected"] - data["total_unc"], data["expected"] + data["total_unc"], facecolor='gold', alpha=0.5, label="68% unc.")
    ax.legend(frameon=False, borderaxespad=0, loc='upper left')
    ax.spines['top'].set_visible(False)
    ax.spines['right'].set_visible(False)
    Y = np.amax(data["grating"])
    ax.set(
            xlabel="Photon energy [eV]",
            ylabel="Intensity",
            ylim=(0, 1.3*Y))
    plt.show()